In [1]:
import matplotlib.pyplot as plt
import numpy as np
import pandas as pd
import requests
import json
import time
import polyline
import folium
from folium.plugins import BeautifyIcon
import math
import osmnx as ox
import ast
import geopandas

from geopy.geocoders import Nominatim
import geopy.distance
from arcgis import geometry
from shapely.geometry import Point, Polygon, LineString

/opt/anaconda3/lib/python3.8/site-packages/geopandas/_compat.py:111: UserWarning: The Shapely GEOS version (3.9.1-CAPI-1.14.2) is incompatible with the GEOS version PyGEOS was compiled with (3.10.1-CAPI-1.16.0). Conversions between both will be slow.
  warnings.warn(


In [2]:
metro = 'Atlanta, GA'

In [3]:
df = pd.read_csv(f'{metro}_segments.csv', index_col=0)
df = df.reset_index(drop=True)
print(df.shape)
df.head()

(332, 15)


id  resource_state                         name  climb_category  \
0    632050               2   Airport Ride - Long Option               0   
1   2940137               2  Airport Ride 40 Mile Option               0   
2   8108123               2                 krog-chester               0   
3  14623223               2              hammer the hill               0   
4    637568               2     McLendon Ave WB (Hill 3)               0   

  climb_category_desc  avg_grade                            start_latlng  \
0                  NC        0.0    [33.7237793114036, -84.421565076336]   
1                  NC       -0.0  [33.74471847899258, -84.4048383180052]   
2                  NC        1.9                 [33.752219, -84.363139]   
3                  NC       -1.7                 [33.781844, -84.369313]   
4                  NC        3.4               [33.7648956, -84.3428774]   

                                end_latlng  elev_difference  distance  \
0     [33.7477141711861, -84.401353038847]             70.6   90657.9   
1  [33.74462309293449, -84.40470739267766]             62.8   64560.5   
2                  [33.752556, -84.359143]              7.9     376.0   
3                  [33.781874, -84.372702]              8.0     307.0   
4                [33.7649679, -84.3480092]             18.5     475.4   

                                              points  starred  \
0  qtylExqgbO`DtDjAhAbAx@|B~AtA|@^RnD|AhBr@lBj@fA...    False   
1  mw}lEfidbObAjAXf@L\jAzF~BdKl@rBf@tAnAfCn@bAf@p...    False   
2                         if_mErd|aOeAiHKkAAg@HgDDwE    False   
3                                o_emEfk}aO@dGGpB?lH    False   
4                                   quamE~exaOQfUBxH    False   

                                   elevation_profile  local_legend_enabled  \
0  https://d3o5xota0a1fcr.cloudfront.net/v6/chart...                  True   
1  https://d3o5xota0a1fcr.cloudfront.net/v6/chart...                  True   
2  https://d3o5xota0a1fcr.cloudfront.net/v6/chart...                  True   
3  https://d3o5xota0a1fcr.cloudfront.net/v6/chart...                  True   
4  https://d3o5xota0a1fcr.cloudfront.net/v6/chart...                  True   

                                    Decoded Polyline  
0  [(33.72377, -84.42157), (33.72296, -84.42248),...  
1  [(33.74471, -84.40484), (33.74437, -84.40522),...  
2  [(33.75221, -84.36314), (33.75256, -84.36165),...  
3  [(33.78184, -84.36932), (33.78183, -84.37063),...  
4  [(33.76489, -84.34288), (33.76498, -84.34644),...

In [4]:
def to_linestring(x):
    lats = [i[0] for i in x]
    longs = [i[1] for i in x]
    
    line_string = LineString(zip(longs, lats))
    return line_string

In [5]:
def linestring_convert(x):
 
    to_polyline = list(x.exterior.coords)
    return [(j, i) for i, j in to_polyline]

In [6]:
def point_convert(x):
    to_point = (x.y, x.x)
    return to_point

In [7]:
df[['Decoded Polyline', 'end_latlng']] = df[['Decoded Polyline', 'end_latlng']].applymap(lambda x: ast.literal_eval(x))
df_geo = geopandas.GeoDataFrame(df['Decoded Polyline'])

In [8]:
df_geo['Decoded Polyline'] = df_geo['Decoded Polyline'].apply(to_linestring)
df_geo = df_geo.set_geometry('Decoded Polyline')

In [9]:
buffer_size = 0.001
df_geo = df_geo.buffer(buffer_size)

df['Buffered Polyline'] = df_geo.apply(linestring_convert)

In [10]:
# df['Buffered Polyline'] 

In [11]:
geolocator = Nominatim(user_agent="drews_app")
location = geolocator.geocode(metro)

In [12]:
#  tile = 'OpenStreetMap'
# tile = 'Stamen Terrain'
# tile = 'Stamen Toner'
# tile = 'Stamen Watercolor'
# tile = 'CartoDB positron'
tile = 'CartoDB dark_matter'

mi = 3
center = (location.latitude, location.longitude)
north = geopy.distance.distance(miles=mi).destination(center, bearing=0)[:2]
east = geopy.distance.distance(miles=mi).destination(center, bearing=90)[:2]
south= geopy.distance.distance(miles=mi).destination(center, bearing=180)[:2]
west = geopy.distance.distance(miles=mi).destination(center, bearing=270)[:2]

z = folium.Map(tiles=tile)
z.fit_bounds([[south[0], west[1]], [north[0], east[1]]])
folium.PolyLine(df['Buffered Polyline'], color='blue').add_to(z)
folium.PolyLine(df['Decoded Polyline'], color='red').add_to(z)
z

In [16]:
df.to_csv(f'{metro}_buffered.csv')

In [17]:
#  tile = 'OpenStreetMap'
# tile = 'Stamen Terrain'
# tile = 'Stamen Toner'
# tile = 'Stamen Watercolor'
# tile = 'CartoDB positron'
tile = 'CartoDB dark_matter'

mi = 3
center = (location.latitude, location.longitude)
north = geopy.distance.distance(miles=mi).destination(center, bearing=0)[:2]
east = geopy.distance.distance(miles=mi).destination(center, bearing=90)[:2]
south= geopy.distance.distance(miles=mi).destination(center, bearing=180)[:2]
west = geopy.distance.distance(miles=mi).destination(center, bearing=270)[:2]

z = folium.Map(tiles=tile)
z.fit_bounds([[south[0], west[1]], [north[0], east[1]]])
# folium.PolyLine(df['Buffered Polyline'], color='blue').add_to(z)
# folium.PolyLine(bound_list, color='red').add_to(z)

# z